In [1]:
import pandas as pd
import numpy as np
import random
from sympy import isprime, nextprime
import os
import pickle
os.chdir('Resources/')

In [2]:
def load_key(filename):
    with open(filename, "rb") as f:
        return pickle.load(f)

In [3]:
def string_to_int(message):
    return int.from_bytes(message.encode('utf-8'), byteorder='big')

def int_to_string(value):
    byte_length = (value.bit_length() + 7) // 8 
    return value.to_bytes(byte_length, byteorder='big').decode('utf-8', errors='ignore')

def float_to_string(message):
    return str(message)

def string_to_float(message):
    return float(message)

In [4]:
def power(b, p, m):
    b = b % m
    if p == 0:
        return 1
    j = power(b, p // 2, m)
    j = (j * j) % m
    if p % 2 == 1:
        j = (j * b) % m
    return j

In [5]:
def mod_inv(a, m):
    origin_m = m
    y, x = 0, 1

    if m == 1:
        return 0

    while a > 1:
        q = a // m
        temp = m

        m = a % m
        a = temp
        temp = y

        y = x - q * y
        x = temp

    if x < 0:
        x += origin_m
    return x

In [6]:
df = pd.read_csv('4_SD_Structured_Data.csv')

private_keys = load_key("3_CC_Private_Key.pkl")
public_keys = load_key("3_CC_Public_Key.pkl")

In [7]:
column_names = [
    "Age", "Sex", "ChestPainType", "RestingBloodPressure", "Cholesterol",
    "FastingBloodSugar", "RestingECG", "MaximumHeartRate", "ExerciseAngina",
    "Oldpeak", "ST_Slope", "HeartDisease"
]

In [9]:
encrypted_data = pd.DataFrame()

for k in range(11):
    public_key = public_keys[k]
    p = public_key['p']
    g = public_key['g']
    h = public_key['h']
        
    print(f"Processing Column: {column_names[k]}")

    y = random.randint(1, p - 2)
    s = power(h, y, p)

    messages = df.iloc[:, k].values 

    encrypted_column = []

    for i, message in enumerate(messages, 1):
        if message is not None and message == message:  
            print(f"Processing Message {i}: {message}")
            
            if isinstance(message, str):
                temp_message = string_to_int(message)
            elif isinstance(message, float):
                temp_message = string_to_int(float_to_string(message))
            else:
                temp_message = int(message)  
            
            c1 = power(g, y, p)
            c2 = (temp_message * s) % p
            
            encrypted_column.append(f"({c1},{c2})") 
            print(f"Ciphertext: (c1, c2): ({c1}, {c2})")
        
        else:
            encrypted_column.append(None)

    encrypted_data[column_names[k]] = encrypted_column

df['HeartDisease'] = df['HeartDisease'].replace({'Yes': 1, 'No': 0})
combined_df = pd.concat([encrypted_data, df['HeartDisease']], axis=1)
combined_df.to_csv('5_SD_Encrypted_Data.csv', index=False)

Processing Column: Age
Processing Message 1: 40
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 43265242834931296564884613226316475267062930985951)
Processing Message 2: 49
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 43327235990578280513604496881228973626857816253398)
Processing Message 3: 37
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 24820413721691715670779596158471911860856494555103)
Processing Message 4: 48
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 18754794891474500637704435342407055205180862768083)
Processing Message 5: 54
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 371958933881903692319301929474990158769311604682)
Processing Message 6: 39
Ciphertext: (c1, c2): (3476488068334709321004428324822234875385570758714, 18692801735827516688984551687494556845385977500636)
Processing Message 7: 45
Ciphertext: (c1, c2): (3476488068334709321004428

C:\Users\USER\AppData\Local\Temp\ipykernel_16324\64534859.py:40: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df['HeartDisease'] = df['HeartDisease'].replace({'Yes': 1, 'No': 0})
